# "Density" statistics & density plot

Statistics "density" are calculated on the sample of a single continuous variable.
It approximates the Probability Density Function (PDF) of this sample.
"Density" statistic samples this function point.
It's weighted, it means the counted density depends on observation weights.

This notebook uses definitions from [DataFrame](https://kotlin.github.io/dataframe/overview.html).

## Usage

"Density" statistic is useful when you have a large dataset,
and you want to understand the underlying probability distribution.
Density plot visualizes the PDF and also allows you to compare the distribution of different samples.
This is a useful alternative to the histogram for continuous data that comes from an underlying smooth distribution.

## Arguments

* Input (mandatory):
    - `x` — numeric sample on which the statistics are calculated
* Weights (optional):
    - `weights` — set of weights of the same size as the input sample.
      `null` (by default) means all weights are equal to `1.0` and the weighted density is equal to the normal one
* Parameters (optional):
    - `n: Int` — number of sampled points;
    - `trim: Boolean` — if `false`, each density is computed on the full range of the data,
      if `true`, each density is computed over the range of that group (only for grouped inputs).
    - `adjust: Double` — adjusts the value of bandwidth by multiplying it; changes how smooth the frequency curve is.
    - `kernel: Kernel` — the kernel used to calculate the density function:
        - `Kernel.GAUSSIAN`
        - `Kernel.RECTANGULAR`
        - `Kernel.TRIANGULAR`
        - `Kernel.BIWEIGHT`
        - `Kernel.EPANECHNIKOV`
        - `Kernel.OPTCOSINE`
    - `fullScanMax: Int` — maximum size of data to use density computation with 'full scan'.
      For bigger data, less accurate but more efficient density computation is applied
    - `bandWidth: BandWidth` — the method (or exact value) of bandwidth:
        - `BandWidth.Method.NRD`
        - `BandWidth.Method.NRD0`
        - `BandWidth.value(value: Double)`

### Generalized signature

The specific signature depends on the function,
but all functions related to "density"
statistic (which will be discussed further below — different variations of `statDensity()`, `densityPlot()`)
have approximately the same signature with the arguments above:

```
statDensityArgs := 
   x, 
   weights = null,
   n: Int = 512,
   trim: Boolean = false,
   adjust: Double = 1.0,
   kernel: Kernel = Kernel.GAUSSIAN,
   fullScanMax: Int = 5000,
   bandWidth: BandWidth = BandWidth.Method.NRD0,
```

The possible types of `x` and `weights` depend on where a certain function is used.
They can be simply `Iterable` (`List`, `Set`, etc.) or a reference to a column in a `DataFrame`
(`String`, `ColumnAccessor`) or the `DataColumn` itself.

## Output statistics

| name                 | type   | description                                 |
|----------------------|--------|---------------------------------------------|
| Stat.x               | Double | `x` coordinate                              |
| Stat.density         | Double | Density estimate                            |
| Stat.densityWeighted | Double | Weighted density                            |
| Stat.scaled          | Double | Density estimate, scaled to maximin of 1.0. |
| Stat.scaledWeighted  | Double | Weighted scaled                             |

## StatDensity plots

In [1]:
%useLatestDescriptors
%use kandy
%use dataframe

import org.apache.commons.math3.distribution.NormalDistribution
import org.apache.commons.math3.distribution.UniformRealDistribution
import org.jetbrains.kotlinx.statistics.dataframe.stat.mean

In [2]:
// To generate the data, we use a standard java math library
// https://commons.apache.org/proper/commons-math/
// Generate sample from normal distribution
val depthList = NormalDistribution(500.0, 100.0).sample(1000).toList()
// Generate sample from uniform distribution
val coeffList = UniformRealDistribution(0.0, 1.0).sample(1000).toList()

In [3]:
// Gather them into the DataFrame
val df = dataFrameOf(
    "depth" to depthList,
    "coeff" to coeffList
)
df.head()

<iframe onload="o_resize_iframe_out_1()" style="width:100%;" class="result_container" id="iframe_out_1" frameBorder="0" srcdoc=" <html>
 <head>
 <style type="text/css">
 :root {
 --background: #fff;
 --background-odd: #f5f5f5;
 --background-hover: #d9edfd;
 --header-text-color: #474747;
 --text-color: #848484;
 --text-color-dark: #000;
 --text-color-medium: #737373;
 --text-color-pale: #b3b3b3;
 --inner-border-color: #aaa;
 --bold-border-color: #000;
 --link-color: #296eaa;
 --link-color-pale: #296eaa;
 --link-hover: #1a466c;
}

:root[theme="dark"], :root [data-jp-theme-light="false"], .dataframe_dark{
 --background: #303030;
 --background-odd: #3c3c3c;
 --background-hover: #464646;
 --header-text-color: #dddddd;
 --text-color: #b3b3b3;
 --text-color-dark: #dddddd;
 --text-color-medium: #b2b2b2;
 --text-color-pale: #737373;
 --inner-border-color: #707070;
 --bold-border-color: #777777;
 --link-color: #008dc0;
 --link-color-pale: #97e1fb;
 --link-hover: #00688e;
}

p.dataframe_description {
 color: var(--text-color-dark);
}

table.dataframe {
 font-family: "Helvetica Neue", Helvetica, Arial, sans-serif;
 font-size: 12px;
 background-color: var(--background);
 color: var(--text-color-dark);
 border: none;
 border-collapse: collapse;
}

table.dataframe th, td {
 padding: 6px;
 border: 1px solid transparent;
 text-align: left;
}

table.dataframe th {
 background-color: var(--background);
 color: var(--header-text-color);
}

table.dataframe td {
 vertical-align: top;
 white-space: nowrap;
}

table.dataframe th.bottomBorder {
 border-bottom-color: var(--bold-border-color);
}

table.dataframe tbody > tr:nth-child(odd) {
 background: var(--background-odd);
}

table.dataframe tbody > tr:nth-child(even) {
 background: var(--background);
}

table.dataframe tbody > tr:hover {
 background: var(--background-hover);
}

table.dataframe a {
 cursor: pointer;
 color: var(--link-color);
 text-decoration: none;
}

table.dataframe tr:hover > td a {
 color: var(--link-color-pale);
}

table.dataframe a:hover {
 color: var(--link-hover);
 text-decoration: underline;
}

table.dataframe img {
 max-width: fit-content;
}

table.dataframe th.complex {
 background-color: var(--background);
 border: 1px solid var(--background);
}

table.dataframe .leftBorder {
 border-left-color: var(--inner-border-color);
}

table.dataframe .rightBorder {
 border-right-color: var(--inner-border-color);
}

table.dataframe .rightAlign {
 text-align: right;
}

table.dataframe .expanderSvg {
 width: 8px;
 height: 8px;
 margin-right: 3px;
}

table.dataframe .expander {
 display: flex;
 align-items: center;
}

/* formatting */

table.dataframe .null {
 color: var(--text-color-pale);
}

table.dataframe .structural {
 color: var(--text-color-medium);
 font-weight: bold;
}

table.dataframe .dataFrameCaption {
 font-weight: bold;
}

table.dataframe .numbers {
 color: var(--text-color-dark);
}

table.dataframe td:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}

table.dataframe tr:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}


:root {
 --scroll-bg: #f5f5f5;
 --scroll-fg: #b3b3b3;
}
:root[theme="dark"], :root [data-jp-theme-light="false"]{
 --scroll-bg: #3c3c3c;
 --scroll-fg: #97e1fb;
}
body {
 scrollbar-color: var(--scroll-fg) var(--scroll-bg);
}
body::-webkit-scrollbar {
 width: 10px; /* Mostly for vertical scrollbars */
 height: 10px; /* Mostly for horizontal scrollbars */
}
body::-webkit-scrollbar-thumb {
 background-color: var(--scroll-fg);
}
body::-webkit-scrollbar-track {
 background-color: var(--scroll-bg);
}
 </style>
 </head>
 <body>
 <table class="dataframe" id="df_-1476395008"></table>

<p class="dataframe_description">DataFrame: rowsCount = 5, columnsCount = 2</p>

 </body>
 <script>
 (function () {
 window.DataFrame = window.DataFrame || new (function () {
 this.addTable = function (df) {
 let cols = df.cols;
 for (let i = 0; i < cols.length; i++) {
 for (let c of cols[i].children) {
 cols[c].parent = i;
 }
 }
 df.nrow = 

`df` has a signature

| depth | coeff |
|-------|-------|

Let's take a look at `StatDensity` output DataFrame:

In [4]:
df.statDensity("depth", "coeff").head(5)

<iframe onload="o_resize_iframe_out_2()" style="width:100%;" class="result_container" id="iframe_out_2" frameBorder="0" srcdoc=" <html>
 <head>
 <style type="text/css">
 :root {
 --background: #fff;
 --background-odd: #f5f5f5;
 --background-hover: #d9edfd;
 --header-text-color: #474747;
 --text-color: #848484;
 --text-color-dark: #000;
 --text-color-medium: #737373;
 --text-color-pale: #b3b3b3;
 --inner-border-color: #aaa;
 --bold-border-color: #000;
 --link-color: #296eaa;
 --link-color-pale: #296eaa;
 --link-hover: #1a466c;
}

:root[theme="dark"], :root [data-jp-theme-light="false"], .dataframe_dark{
 --background: #303030;
 --background-odd: #3c3c3c;
 --background-hover: #464646;
 --header-text-color: #dddddd;
 --text-color: #b3b3b3;
 --text-color-dark: #dddddd;
 --text-color-medium: #b2b2b2;
 --text-color-pale: #737373;
 --inner-border-color: #707070;
 --bold-border-color: #777777;
 --link-color: #008dc0;
 --link-color-pale: #97e1fb;
 --link-hover: #00688e;
}

p.dataframe_description {
 color: var(--text-color-dark);
}

table.dataframe {
 font-family: "Helvetica Neue", Helvetica, Arial, sans-serif;
 font-size: 12px;
 background-color: var(--background);
 color: var(--text-color-dark);
 border: none;
 border-collapse: collapse;
}

table.dataframe th, td {
 padding: 6px;
 border: 1px solid transparent;
 text-align: left;
}

table.dataframe th {
 background-color: var(--background);
 color: var(--header-text-color);
}

table.dataframe td {
 vertical-align: top;
 white-space: nowrap;
}

table.dataframe th.bottomBorder {
 border-bottom-color: var(--bold-border-color);
}

table.dataframe tbody > tr:nth-child(odd) {
 background: var(--background-odd);
}

table.dataframe tbody > tr:nth-child(even) {
 background: var(--background);
}

table.dataframe tbody > tr:hover {
 background: var(--background-hover);
}

table.dataframe a {
 cursor: pointer;
 color: var(--link-color);
 text-decoration: none;
}

table.dataframe tr:hover > td a {
 color: var(--link-color-pale);
}

table.dataframe a:hover {
 color: var(--link-hover);
 text-decoration: underline;
}

table.dataframe img {
 max-width: fit-content;
}

table.dataframe th.complex {
 background-color: var(--background);
 border: 1px solid var(--background);
}

table.dataframe .leftBorder {
 border-left-color: var(--inner-border-color);
}

table.dataframe .rightBorder {
 border-right-color: var(--inner-border-color);
}

table.dataframe .rightAlign {
 text-align: right;
}

table.dataframe .expanderSvg {
 width: 8px;
 height: 8px;
 margin-right: 3px;
}

table.dataframe .expander {
 display: flex;
 align-items: center;
}

/* formatting */

table.dataframe .null {
 color: var(--text-color-pale);
}

table.dataframe .structural {
 color: var(--text-color-medium);
 font-weight: bold;
}

table.dataframe .dataFrameCaption {
 font-weight: bold;
}

table.dataframe .numbers {
 color: var(--text-color-dark);
}

table.dataframe td:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}

table.dataframe tr:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}


:root {
 --scroll-bg: #f5f5f5;
 --scroll-fg: #b3b3b3;
}
:root[theme="dark"], :root [data-jp-theme-light="false"]{
 --scroll-bg: #3c3c3c;
 --scroll-fg: #97e1fb;
}
body {
 scrollbar-color: var(--scroll-fg) var(--scroll-bg);
}
body::-webkit-scrollbar {
 width: 10px; /* Mostly for vertical scrollbars */
 height: 10px; /* Mostly for horizontal scrollbars */
}
body::-webkit-scrollbar-thumb {
 background-color: var(--scroll-fg);
}
body::-webkit-scrollbar-track {
 background-color: var(--scroll-bg);
}
 </style>
 </head>
 <body>
 <table class="dataframe" id="df_-1476395006"></table>

<p class="dataframe_description">DataFrame: rowsCount = 5, columnsCount = 1</p>

 </body>
 <script>
 (function () {
 window.DataFrame = window.DataFrame || new (function () {
 this.addTable = function (df) {
 let cols = df.cols;
 for (let i = 0; i < cols.length; i++) {
 for (let c of cols[i].children) {
 cols[c].parent = i;
 }
 }
 df.nrow = 

It has the following signature:

<table>
  <thead>
    <tr>
      <th alignt="left" colspan="5">Stat</th>
    </tr>
  </thead>
  <thead>
    <tr>
      <th>x</th>
      <th>density</th>
      <th>densityWeighted</th>
      <th>scaled</th>
      <th>scaledWeighted</th>
    </tr>
  </thead>
</table>

As you can see, we got a `DataFrame` with one `ColumnGroup` called `Stat` which contains several columns with statics.
For `statDensity`, each row corresponds to one PDF point.
`Stat.x` is the column with this point `x` coordinate.
`Stat.density` contains the estimated density.
`Stat.densityWeighted` — weighted version of `density`.
`Stat.scaled` is a density scaled to a maximum of 1.0.
`Stat.scaledWeighted` — weighted version of `scaled`.
`DataFrame` with "density" statistics is called `StatDensityFrame`

### `statDensity` transform

`statDensity(statDensityArgs) { /*new plotting context*/ }` modifies a plotting context —
instead of original data (no matter was it empty or not) new `StatDensity` dataset
(calculated on given arguments, inputs and weights can be provided as `Iterable` or as dataset column reference —
by name as a `String`, as a `ColumnReference` or as a `DataColumn`) is used inside a new context
(original dataset and primary context are not affected —
you can add layers using initial dataset outside the `statDensity` context).
Since the old dataset is irrelevant, we cannot use references for its columns.
But we can refer to the new ones.
They are all contained in the `Stat` group and can be called inside the new context:

In [5]:
plot {
    statDensity(depthList, adjust = 0.2) {
        // New `StatDensity` dataset here
        line {
            // Use `Stat.*` columns for mappings
            x(Stat.x)
            y(Stat.density)
            color(Stat.density)
        }
    }
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.5.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="ZizZSb"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 
 (function() {
 // ----------
 
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"color",
"scale_mapper_kind":"color_gradient",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"color":"density"
},
"stat":"identity",
"data":{
"density":[9.152841808549078E-5,8.921080880098606E-5,8.176727672523061E-5,7.21879621192177E-5,6.418185312791295E-5,6.108164165441228E-5,6.491545999803586E-5,7.591214182271793E-5,9.252251660561075E-5,1.1188034368632528E-4,1.3052232638596084E-4,1.4514586751162027E-4,1.5321871709791178E-4,1.533550072233042E-4,1.454751656006904E-4,1.3080101951122952E-4,1.1169630087511814E-4,9.131882230290956E-5,7.307457057881825E-5,5.9947330833148034E-5,5.384969073519708E-5,5.5154392213763665E-5,6.253454775636791E-5,7.31985462869351E-5,8.353811610387978E-5,9.00804863782327E-5,9.047047719695401E-5,8.411571197709215E-5,7.22205302255472E-5,5.7203076551872494E-5,4.178075615587569E-5,2.8135845390763413E-5,1.746793512291705E-5,9.997915302152267E-6,5.2754427190873935E-6,2.566185481146538E-6,1.1507899995371069E-6,4.757542840746938E-7,1.8132087379577907E-7,6.370761032359896E-8,2.0635415702174394E-8,6.16188397873069E-9,1.6962591401021192E-9,4.3047650904317993E-10,1.007143844954347E-10,2.1733430799112996E-11,4.396315209980298E-12,1.270462482955758E-12,2.871279306996204E-12,1.4460681392887893E-11,7.027216489020964E-11,3.1548748816321164E-10,1.3068869865510453E-9,4.995343298687538E-9,1.761987800383763E-8,5.73589540609811E-8,1.723559777345256E-7,4.781517786307071E-7,1.2250017814610992E-6,2.899329199628426E-6,6.342541772829657E-6,1.2832977621162516E-5,2.403754700014461E-5,4.1734683334241016E-5,6.728046977975085E-5,1.0094001225752948E-4,1.4136667876132623E-4,1.855550343513193E-4,2.294262543677337E-4,2.688779976652944E-4,3.0084644865299156E-4,3.238988208462789E-4,3.3813804248121075E-4,3.4457696833450696E-4,3.443800129545206E-4,3.3835884822596E-4,3.2691068469037625E-4,3.1034282373384835E-4,2.8934220073626425E-4,2.652864610444747E-4,2.4019318977628473E-4,2.163386966651954E-4,1.9580050907655298E-4,1.8019676783909196E-4,1.7066455620223667E-4,1.678386352290818E-4,1.7155958348445346E-4,1.8035211590710696E-4,1.9112140644651063E-4,1.9961354706824022E-4,2.0178964205599007E-4,1.956083943053784E-4,1.82289986506721E-4,1.6628752311373862E-4,1.538417479221927E-4,1.507204024458083E-4,1.601191848339263E-4,1.8157121174956065E-4,2.1121653044425787E-4,2.4320019402887188E-4,2.7155202550712256E-4,2.918063934855382E-4,3.018563355836319E-4,3.019543844874635E-4,2.9413039415762747E-4,2.8141692817727445E-4,2.671686034713639E-4,2.5459615815078E-4,2.4654654721289755E-4,2.4553697738676183E-4,2.539914219125812E-4,2.7449366605798394E-4,3.097579400706448E-4,3.6207253634078186E-4,4.3223570027095304E-4,5.183459521652624E-4,6.150086493879261E-4,7.134328440676308E-4,8.025684758547727E-4,8.710736501598846E-4,9.096748098303146E-4,9.13395355379078E-4,8.830900225209038E-4,8.257361176154629E-4,7.531537022993733E-4,6.793589989202654E-4,6.173977344255127E-4,5.767981632415742E-4,5.624101480231956E-4,5.745590351074148E-4,6.097761156554578E-4,6.614002560276989E-4,7.200092163473395E-4,7.743094455702785E-4,8.1315009056716E-4,8.286125881403454E-4,8.191447719038308E-4,7.911684597695243E-4,7.579498810732307E-4,7.357105342944573E-4,7.383827295092593E-4,7.732500279616499E-4,8.393593473138107E-4,9.291350717494614E-4,0.0010319210992591732,0.0011373444292297405,0.0012369886677371046,0.0013243838362770313,0.0013945448276765251,0.0014442864637620367,0.001473438210678043,0.001485931083074843,0.0014895

### DensityPlot layer

Density plot is a statistical plot used for visualizing the distribution of continuous variables.
It's an area graph of kernel-estimated PDF.
So basically, we can build a histogram with `statDensity` as follows:

In [6]:
val statDensityAndAreaPlot = df.plot {
    statDensity("depth") {
        area {
            x(Stat.x)
            y(Stat.density)
        }
    }
    layout.title = "`statDensity()` + `area()` layer"
}
statDensityAndAreaPlot

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.5.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="I1oYgj"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 
 (function() {
 // ----------
 
 var plotSpec={
"ggtitle":{
"text":"`statDensity()` + `area()` layer"
},
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density"
},
"stat":"identity",
"data":{
"density":[5.230453106561777E-5,5.3911617195861116E-5,5.5429408858707796E-5,5.684832419092773E-5,5.815934934544032E-5,5.9354149521594184E-5,6.0425175806032464E-5,6.136576648148915E-5,6.217024154116761E-5,6.283398924626051E-5,6.335354368094423E-5,6.372665238966932E-5,6.39523333223435E-5,6.403092046041357E-5,6.396409764718019E-5,6.375492029523355E-5,6.340782478914414E-5,6.29286255392248E-5,6.232449976941949E-5,6.160396023678779E-5,6.0776816179834433E-5,5.985412287692605E-5,5.8848120263784604E-5,5.777216111083256E-5,5.6640629297998836E-5,5.546884874820338E-5,5.4272983593500015E-5,5.3069930152738465E-5,5.1877201300018556E-5,5.0712803802928126E-5,4.959510921248584E-5,4.8542718896800274E-5,4.757432383141776E-5,4.6708559794512225E-5,4.5963858667210076E-5,4.535829661042406E-5,4.490943998059124E-5,4.463418995761896E-5,4.454862698784E-5,4.466785629031035E-5,4.5005855832497786E-5,4.557532834619024E-5,4.6387559120014564E-5,4.745228146400851E-5,4.877755188612248E-5,5.036963714171528E-5,5.2232915406176036E-5,5.4369793869025694E-5,5.678064504699298E-5,5.946376405627345E-5,6.241534896441358E-5,6.562950615558034E-5,6.909828238691663E-5,7.281172488800266E-5,7.67579704623304E-5,8.092336409386244E-5,8.529260705044237E-5,8.984893391878795E-5,9.457431741499969E-5,9.944969920394289E-5,1.0445524434605878E-4,1.0957061638782996E-4,1.147752695395567E-4,1.2004875385858596E-4,1.253710288944428E-4,1.3072278086994336E-4,1.3608573818321132E-4,1.4144297983106227E-4,1.467792312833601E-4,1.5208114238648635E-4,1.5733754204450234E-4,1.625396647180381E-4,1.6768134418912526E-4,1.7275917055752302E-4,1.777726070499674E-4,1.8272406392493034E-4,1.876189275263667E-4,1.9246554336329892E-4,1.9727515294948103E-4,2.0206178500964788E-4,2.0684210252691715E-4,2.1163520795091704E-4,2.1646240969047927E-4,2.213469537617305E-4,2.2631372513734943E-4,2.3138892393278812E-4,2.3659972205948698E-4,2.4197390636495069E-4,2.475395145584056E-4,2.53324470384226E-4,2.593562245509151E-4,2.6566140785058945E-4,2.722655027136964E-4,2.791925391388855E-4,2.86464820522635E-4,2.941026843930051E-4,3.021243024336988E-4,3.1054552347662133E-4,3.193797623530276E-4,3.2863793663616273E-4,3.3832845239446465E-4,3.4845723911805385E-4,3.5902783299781487E-4,3.7004150674309734E-4,3.8149744313929545E-4,3.933929485901561E-4,4.057237019822907E-4,4.1848403337230064E-4,4.3166722625162404E-4,4.45265836511744E-4,4.592720207324154E-4,4.7367786606642765E-4,4.884757138114718E-4,5.036584687552726E-4,5.192198865626187E-4,5.351548318460051E-4,5.514595001240097E-4,5.681315976164994E-4,5.851704737411224E-4,6.025772022432814E-4,6.203546080889071E-4,6.385072385477908E-4,6.570412782628412E-4,6.75964409501988E-4,6.95285620186767E-4,7.150149636461187E-4,7.35163275317031E-4,7.557418527678699E-4,7.767621064215682E-4,7.982351891732656E-4,8.201716137056374E-4,8.425808666851457E-4,8.654710291615528E-4,8.888484123857922E-4,9.127172179098172E-4,9.370792302463626E-4,9.619335495634301E-4,9.872763708913968E-4,0.0010131008151600214,0.0010393968160921213,0.0010661510655991982,0.0010933470188925207,0.0011209649590824596,0.0011489821196317383,0.0011773728616936991,0.0012061089021424061,0.0012351595870198156,0.0012644922042142107,0.001294072328465457,0.0013238641912813288,0.001353831068053578,0.0013839356745838048,0.0014141405653614872,0.0014444085262676459,0.001474702954

But we can do it even faster with `densityPlot(statDensityArgs)` method:

In [7]:
val densityLayerPlot = plot {
    densityPlot(depthList)
    layout.title = "`densityPlot()` layer"
}
densityLayerPlot

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.5.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="Y8xZmu"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 
 (function() {
 // ----------
 
 var plotSpec={
"ggtitle":{
"text":"`densityPlot()` layer"
},
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"x",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density"
},
"stat":"identity",
"data":{
"density":[5.230453106561777E-5,5.3911617195861116E-5,5.5429408858707796E-5,5.684832419092773E-5,5.815934934544032E-5,5.9354149521594184E-5,6.0425175806032464E-5,6.136576648148915E-5,6.217024154116761E-5,6.283398924626051E-5,6.335354368094423E-5,6.372665238966932E-5,6.39523333223435E-5,6.403092046041357E-5,6.396409764718019E-5,6.375492029523355E-5,6.340782478914414E-5,6.29286255392248E-5,6.232449976941949E-5,6.160396023678779E-5,6.0776816179834433E-5,5.985412287692605E-5,5.8848120263784604E-5,5.777216111083256E-5,5.6640629297998836E-5,5.546884874820338E-5,5.4272983593500015E-5,5.3069930152738465E-5,5.1877201300018556E-5,5.0712803802928126E-5,4.959510921248584E-5,4.8542718896800274E-5,4.757432383141776E-5,4.6708559794512225E-5,4.5963858667210076E-5,4.535829661042406E-5,4.490943998059124E-5,4.463418995761896E-5,4.454862698784E-5,4.466785629031035E-5,4.5005855832497786E-5,4.557532834619024E-5,4.6387559120014564E-5,4.745228146400851E-5,4.877755188612248E-5,5.036963714171528E-5,5.2232915406176036E-5,5.4369793869025694E-5,5.678064504699298E-5,5.946376405627345E-5,6.241534896441358E-5,6.562950615558034E-5,6.909828238691663E-5,7.281172488800266E-5,7.67579704623304E-5,8.092336409386244E-5,8.529260705044237E-5,8.984893391878795E-5,9.457431741499969E-5,9.944969920394289E-5,1.0445524434605878E-4,1.0957061638782996E-4,1.147752695395567E-4,1.2004875385858596E-4,1.253710288944428E-4,1.3072278086994336E-4,1.3608573818321132E-4,1.4144297983106227E-4,1.467792312833601E-4,1.5208114238648635E-4,1.5733754204450234E-4,1.625396647180381E-4,1.6768134418912526E-4,1.7275917055752302E-4,1.777726070499674E-4,1.8272406392493034E-4,1.876189275263667E-4,1.9246554336329892E-4,1.9727515294948103E-4,2.0206178500964788E-4,2.0684210252691715E-4,2.1163520795091704E-4,2.1646240969047927E-4,2.213469537617305E-4,2.2631372513734943E-4,2.3138892393278812E-4,2.3659972205948698E-4,2.4197390636495069E-4,2.475395145584056E-4,2.53324470384226E-4,2.593562245509151E-4,2.6566140785058945E-4,2.722655027136964E-4,2.791925391388855E-4,2.86464820522635E-4,2.941026843930051E-4,3.021243024336988E-4,3.1054552347662133E-4,3.193797623530276E-4,3.2863793663616273E-4,3.3832845239446465E-4,3.4845723911805385E-4,3.5902783299781487E-4,3.7004150674309734E-4,3.8149744313929545E-4,3.933929485901561E-4,4.057237019822907E-4,4.1848403337230064E-4,4.3166722625162404E-4,4.45265836511744E-4,4.592720207324154E-4,4.7367786606642765E-4,4.884757138114718E-4,5.036584687552726E-4,5.192198865626187E-4,5.351548318460051E-4,5.514595001240097E-4,5.681315976164994E-4,5.851704737411224E-4,6.025772022432814E-4,6.203546080889071E-4,6.385072385477908E-4,6.570412782628412E-4,6.75964409501988E-4,6.95285620186767E-4,7.150149636461187E-4,7.35163275317031E-4,7.557418527678699E-4,7.767621064215682E-4,7.982351891732656E-4,8.201716137056374E-4,8.425808666851457E-4,8.654710291615528E-4,8.888484123857922E-4,9.127172179098172E-4,9.370792302463626E-4,9.619335495634301E-4,9.872763708913968E-4,0.0010131008151600214,0.0010393968160921213,0.0010661510655991982,0.0010933470188925207,0.0011209649590824596,0.0011489821196317383,0.0011773728616936991,0.0012061089021424061,0.0012351595870198156,0.0012644922042142107,0.001294072328465457,0.0013238641912813288,0.001353831068053578,0.0013839356745838048,0.0014141405653

Let's compare them:

In [8]:
plotGrid(listOf(statDensityAndAreaPlot, densityLayerPlot))

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.5.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="pX46zI"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 
 (function() {
 // ----------
 
 var plotSpec={
"layout":{
"name":"grid",
"ncol":2,
"nrow":1,
"fit":true,
"align":false
},
"figures":[{
"ggtitle":{
"text":"`statDensity()` + `area()` layer"
},
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density"
},
"stat":"identity",
"data":{
"density":[5.230453106561777E-5,5.3911617195861116E-5,5.5429408858707796E-5,5.684832419092773E-5,5.815934934544032E-5,5.9354149521594184E-5,6.0425175806032464E-5,6.136576648148915E-5,6.217024154116761E-5,6.283398924626051E-5,6.335354368094423E-5,6.372665238966932E-5,6.39523333223435E-5,6.403092046041357E-5,6.396409764718019E-5,6.375492029523355E-5,6.340782478914414E-5,6.29286255392248E-5,6.232449976941949E-5,6.160396023678779E-5,6.0776816179834433E-5,5.985412287692605E-5,5.8848120263784604E-5,5.777216111083256E-5,5.6640629297998836E-5,5.546884874820338E-5,5.4272983593500015E-5,5.3069930152738465E-5,5.1877201300018556E-5,5.0712803802928126E-5,4.959510921248584E-5,4.8542718896800274E-5,4.757432383141776E-5,4.6708559794512225E-5,4.5963858667210076E-5,4.535829661042406E-5,4.490943998059124E-5,4.463418995761896E-5,4.454862698784E-5,4.466785629031035E-5,4.5005855832497786E-5,4.557532834619024E-5,4.6387559120014564E-5,4.745228146400851E-5,4.877755188612248E-5,5.036963714171528E-5,5.2232915406176036E-5,5.4369793869025694E-5,5.678064504699298E-5,5.946376405627345E-5,6.241534896441358E-5,6.562950615558034E-5,6.909828238691663E-5,7.281172488800266E-5,7.67579704623304E-5,8.092336409386244E-5,8.529260705044237E-5,8.984893391878795E-5,9.457431741499969E-5,9.944969920394289E-5,1.0445524434605878E-4,1.0957061638782996E-4,1.147752695395567E-4,1.2004875385858596E-4,1.253710288944428E-4,1.3072278086994336E-4,1.3608573818321132E-4,1.4144297983106227E-4,1.467792312833601E-4,1.5208114238648635E-4,1.5733754204450234E-4,1.625396647180381E-4,1.6768134418912526E-4,1.7275917055752302E-4,1.777726070499674E-4,1.8272406392493034E-4,1.876189275263667E-4,1.9246554336329892E-4,1.9727515294948103E-4,2.0206178500964788E-4,2.0684210252691715E-4,2.1163520795091704E-4,2.1646240969047927E-4,2.213469537617305E-4,2.2631372513734943E-4,2.3138892393278812E-4,2.3659972205948698E-4,2.4197390636495069E-4,2.475395145584056E-4,2.53324470384226E-4,2.593562245509151E-4,2.6566140785058945E-4,2.722655027136964E-4,2.791925391388855E-4,2.86464820522635E-4,2.941026843930051E-4,3.021243024336988E-4,3.1054552347662133E-4,3.193797623530276E-4,3.2863793663616273E-4,3.3832845239446465E-4,3.4845723911805385E-4,3.5902783299781487E-4,3.7004150674309734E-4,3.8149744313929545E-4,3.933929485901561E-4,4.057237019822907E-4,4.1848403337230064E-4,4.3166722625162404E-4,4.45265836511744E-4,4.592720207324154E-4,4.7367786606642765E-4,4.884757138114718E-4,5.036584687552726E-4,5.192198865626187E-4,5.351548318460051E-4,5.514595001240097E-4,5.681315976164994E-4,5.851704737411224E-4,6.025772022432814E-4,6.203546080889071E-4,6.385072385477908E-4,6.570412782628412E-4,6.75964409501988E-4,6.95285620186767E-4,7.150149636461187E-4,7.35163275317031E-4,7.557418527678699E-4,7.767621064215682E-4,7.982351891732656E-4,8.201716137056374E-4,8.425808666851457E-4,8.654710291615528E-4,8.888484123857922E-4,9.127172179098172E-4,9.370792302463626E-4,9.619335495634301E-4,9.872763708913968E-4,0.0010131008151600214,0.0010393968160921213,0.0010661510655991982,0.0010933470188925207,0.0011209649590824596,0.0011489821196317383,0.0011773728616936991,0.0012061089021424061,0.0012351595870198156,0.0012644922042142107,0.001294072328465457,0.0013238641912813288,0.00135383106

These two plots are identical.
Indeed, `densityPlot` just uses `statDensity` and `area` and performs coordinate mappings under the hood.
And we can customize `densityPlot` layer: `densityPlot()` optionally opens a new context,
where we can configure bars (as in the usual context opened by `area { ... }`) —
even change coordinate mappings from default ones.
`StatDensity` dataset of `densityPlot` is also can be accessed here.

In [9]:
df.plot {
    densityPlot(depth) {
        // Change a column mapped on `y` to `Stat.scaled`
        y(Stat.scaled)
        alpha = 0.7
        fillColor = Color.RED
        borderLine.color = Color.BLACK
    }
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.5.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="ycFtfs"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 
 (function() {
 // ----------
 
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"depth",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"scaled"
},
"stat":"identity",
"data":{
"scaled":[0.013191277855444229,0.01359658728561721,0.013979376522866457,0.014337229007523697,0.014667871434409356,0.01496920175482857,0.015239316121990854,0.015476534441234046,0.015679424206686308,0.015846822331196962,0.015977854705817494,0.01607195325802331,0.016128870313370697,0.01614869010246021,0.016131837292990645,0.016079082464405477,0.015991544479265003,0.01587068974020088,0.015718328353399834,0.015536607248418459,0.015328000329295856,0.01509529575311387,0.014841580449240797,0.014570222005554669,0.01428484805723194,0.01398932331964151,0.013687724410102573,0.013384312604495815,0.013083504674821516,0.012789841953726969,0.012507957772764623,0.012242543423687082,0.011998312797371439,0.011779965863838195,0.011592151169979623,0.011439427549539222,0.011326225262839528,0.011256806811726952,0.011235227707861645,0.011265297509183906,0.011350541479164516,0.01149416326500428,0.01169900903270302,0.011967533537031415,0.012301768640865447,0.01270329482890704,0.013173216283277342,0.013712140100630783,0.014320160230221366,0.01499684669790502,0.015741240650856567,0.016551855710698407,0.01742668605815938,0.018363221590245272,0.01935847039175863,0.020408988648043244,0.021510917996876947,0.022660030176951184,0.023851778681375394,0.025081356970656686,0.026343762644551048,0.027633866820273814,0.02894648782015449,0.0302764681392854,0.03161875354727432,0.03296847308177669,0.034321018618557304,0.03567212265631081,0.03701793293659933,0.03835508253150655,0.03968075407459263,0.04099273688423922,0.04228947583141867,0.0435701109343929,0.0448345068181738,0.046083271353409665,0.04731776298378186,0.04854008645865181,0.049753076903933546,0.050960272384153515,0.05216587532758565,0.05337470339946146,0.05459213061109183,0.055824019641130235,0.057076646515426495,0.05835661894072668,0.05967078971212084,0.061026166712457634,0.062429821092272186,0.06388879526000028,0.06541001232375161,0.06700018860754559,0.06866575081693937,0.07041275935210466,0.07224683916166583,0.07417311939940875,0.07619618299006184,0.07832002703179397,0.08054803476431423,0.08288295961527506,0.08532692160720944,0.08788141616604182,0.09054733512419201,0.09332499946078586,0.09621420307312611,0.09921426663236912,0.10232410034751226,0.10554227425068707,0.10886709442878795,0.1122966834669555,0.11582906324333908,0.1194622381265076,0.12319427658073918,0.12702338918330774,0.13094800110390475,0.13496681719042591,0.1390788779471925,0.14328360487956063,0.1475808339097267,0.1519708358378235,0.15645432312431592,0.1610324425971763,0.16570675403222865,0.17047919490847827,0.1753520319926451,0.18032780074872667,0.18540923388949343,0.19059918067791298,0.19590051883903695,0.2013160611490374,0.20684845892158366,0.21250010470758232,0.2182730365593896,0.2241688461835553,0.23018859321751636,0.23633272771794742,0.24260102274592618,0.24899251868264896,0.25550548061672107,0.26213736981857977,0.2688848299691923,0.2757436884490788,0.28270897263035705,0.2897749407596282,0.29693512668294214,0.3041823973553171,0.31150902180450873,0.31890674998896046,0.32636689980862393,0.3338804503983887,0.34143813975931,0.34903056476300315,0.35664828159793466,0.3642819048098503,0.37192220321756525,0.37956019115383643,0.38718721368197584,0.3947950246644527,0.4023758568013949,0.4099224830061805,0.41742826873354744,0.42488721511467153,0.4322939929758736,0.439643968

If we specify weights, `Stat.densityWeighted` is mapped to `y` by default:

In [10]:
df.plot {
    densityPlot(depth, coeff, n = 700, adjust = 0.8, bandWidth = BandWidth.value(17.0))
    // We can add other layers as well.
    // Let's add a horizontal mark line with constant y intercept:
    vLine {
        // Count sample mean
        val mean = depth.mean()
        xIntercept.constant(mean)
        tooltips { line("Depth mean: ${String.format("%.2f", mean)}m") }
        color = Color.RED; width = 2.0
    }
    x.axis.name = "depth, m"
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.5.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="L5rRRd"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 
 (function() {
 // ----------
 
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"depth",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"x",
"name":"depth, m",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"densityWeighted"
},
"stat":"identity",
"data":{
"x":[158.58602236898395,159.50487660582235,160.42373084266075,161.34258507949914,162.26143931633754,163.18029355317594,164.0991477900143,165.0180020268527,165.9368562636911,166.8557105005295,167.7745647373679,168.6934189742063,169.6122732110447,170.5311274478831,171.4499816847215,172.36883592155988,173.28769015839828,174.20654439523668,175.12539863207508,176.04425286891347,176.96310710575187,177.88196134259027,178.80081557942867,179.71966981626707,180.63852405310547,181.55737828994387,182.47623252678224,183.39508676362064,184.31394100045904,185.23279523729744,186.15164947413584,187.07050371097424,187.98935794781264,188.90821218465103,189.8270664214894,190.7459206583278,191.6647748951662,192.5836291320046,193.502483368843,194.4213376056814,195.3401918425198,196.2590460793582,197.1779003161966,198.096754553035,199.0156087898734,199.9344630267118,200.85331726355017,201.77217150038857,202.69102573722697,203.60987997406536,204.52873421090376,205.44758844774216,206.36644268458056,207.28529692141893,208.20415115825733,209.12300539509573,210.04185963193413,210.96071386877253,211.87956810561093,212.79842234244933,213.71727657928773,214.63613081612613,215.55498505296453,216.47383928980292,217.39269352664132,218.31154776347972,219.2304020003181,220.1492562371565,221.0681104739949,221.9869647108333,222.9058189476717,223.8246731845101,224.74352742134846,225.66238165818686,226.58123589502526,227.50009013186366,228.41894436870206,229.33779860554046,230.25665284237886,231.17550707921725,232.09436131605565,233.01321555289405,233.93206978973245,234.85092402657085,235.76977826340925,236.68863250024765,237.60748673708605,238.52634097392442,239.44519521076282,240.36404944760122,241.28290368443962,242.20175792127802,243.1206121581164,244.0394663949548,244.95832063179319,245.87717486863158,246.79602910546998,247.71488334230838,248.63373757914678,249.55259181598518,250.47144605282358,251.39030028966198,252.30915452650038,253.22800876333878,254.14686300017718,255.06571723701558,255.98457147385395,256.9034257106923,257.8222799475308,258.7411341843691,259.6599884212076,260.5788426580459,261.4976968948843,262.4165511317227,263.3354053685611,264.2542596053995,265.1731138422379,266.0919680790763,267.0108223159147,267.9296765527531,268.8485307895915,269.7673850264299,270.6862392632683,271.6050935001067,272.5239477369451,273.4428019737835,274.36165621062185,275.2805104474603,276.19936468429864,277.1182189211371,278.03707315797544,278.95592739481384,279.87478163165224,280.79363586849064,281.71249010532904,282.63134434216744,283.55019857900584,284.46905281584424,285.38790705268264,286.30676128952103,287.22561552635943,288.14446976319783,289.06332400003623,289.9821782368746,290.90103247371303,291.8198867105514,292.73874094738983,293.65759518422817,294.5764494210666,295.49530365790497,296.4141578947434,297.33301213158177,298.2518663684202,299.17072060525857,300.08957484209697,301.00842907893536,301.92728331577376,302.84613755261216,303.76499178945056,304.68384602628896,305.60270026312736,306.52155449996576,307.44040873680416,308.35926297364256,309.2781172104809,310.19697144731936,311.1158256841577,312.03467992099615,312.9535341578345,313.87238839467295,314.7912426315113,315.71009686834975,316.6289511051881,317.5478053

### `densityPlot` plot

`densityPlot(statDensityArgs)` and `DataFrame.densityPlot(statDensityArgs)`
are a family of functions for fast plotting a density plot.

In [11]:
densityPlot(depthList, kernel = Kernel.COSINE)

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.5.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="8Fjh1J"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 
 (function() {
 // ----------
 
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"x",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density"
},
"stat":"identity",
"data":{
"density":[6.423486979074149E-5,7.021974442933431E-5,7.613573268911263E-5,8.179339051630647E-5,8.701154621371744E-5,9.162310199056022E-5,9.548038483225283E-5,9.845987534254537E-5,1.0046616312918327E-4,1.0172486069196617E-4,1.0262820497899155E-4,1.0315143912343377E-4,1.0327780792006896E-4,1.0300326473863809E-4,1.0233660110659881E-4,1.0129916518344858E-4,9.992417814174184E-5,9.825567034591215E-5,9.626747941441215E-5,9.347947027271952E-5,8.987774285602482E-5,8.557763306636694E-5,8.07168406750164E-5,7.545101984738359E-5,6.994879472540532E-5,6.438635968035041E-5,5.894183714882542E-5,5.378957372753147E-5,4.909455717941914E-5,4.469036416637983E-5,4.0309828783591685E-5,3.6091621418879554E-5,3.2170819132529085E-5,2.8344130026375133E-5,2.4337230724700705E-5,2.027756768821783E-5,1.6295141009692145E-5,1.2517477489498223E-5,9.065546923318592E-6,6.0498883607718795E-6,3.5670703814070147E-6,1.6965987384695003E-6,4.983703950599963E-7,1.0755480521298675E-8,0.0,0.0,0.0,0.0,0.0,0.0,0.0,0.0,2.0672544753457962E-7,1.476630509852749E-6,4.152395216544836E-6,8.148335199976427E-6,1.3557517144946446E-5,2.0731662368571936E-5,2.997955415020854E-5,4.117371885657038E-5,5.4008733903509764E-5,6.860799608066949E-5,8.488099796905944E-5,1.0278202802131963E-4,1.2175116702538989E-4,1.4118097790877018E-4,1.604492717866786E-4,1.7921765585100544E-4,1.9732742300828028E-4,2.1420430251569366E-4,2.2930785643988862E-4,2.4215443296208352E-4,2.5233265406282145E-4,2.595775798110126E-4,2.6455022015584766E-4,2.6759042818775425E-4,2.6860090444104904E-4,2.6754929105610566E-4,2.6446926320161825E-4,2.5945945071538545E-4,2.5268027974167007E-4,2.443488355034426E-4,2.3473444121048395E-4,2.2457676985923478E-4,2.1498128929349532E-4,2.0649389192494767E-4,1.9940653647862453E-4,1.94267190790851E-4,1.9061890439805803E-4,1.8857011957095908E-4,1.8847516658647577E-4,1.9015124865807712E-4,1.9301092239405165E-4,1.968293631077141E-4,2.016105825500266E-4,2.0716491999012658E-4,2.129200661495882E-4,2.1885957769415332E-4,2.243537100113471E-4,2.2921104941745892E-4,2.337461706224107E-4,2.3868437735418067E-4,2.4482411245582166E-4,2.522974347668661E-4,2.618124901171914E-4,2.7410783569754507E-4,2.904305160075478E-4,3.111651916033021E-4,3.3638508101597005E-4,3.6448484323119563E-4,3.939934037108817E-4,4.240745736871536E-4,4.5482081664542954E-4,4.8562234185266684E-4,5.160373340520271E-4,5.451856012490742E-4,5.722006436269418E-4,5.976276090406538E-4,6.21483436273442E-4,6.430344790380168E-4,6.621875424729473E-4,6.80210452252439E-4,6.963190301475541E-4,7.097466329480121E-4,7.196709993036918E-4,7.254406672150334E-4,7.273542007853713E-4,7.271189458135363E-4,7.254737613666583E-4,7.233635120018936E-4,7.219673158446151E-4,7.21417198255992E-4,7.222946117318718E-4,7.275266694996568E-4,7.387528396821967E-4,7.563324217847832E-4,7.794606226710987E-4,8.075705453703335E-4,8.401971744142869E-4,8.766442855172435E-4,9.164601154457345E-4,9.577784560048332E-4,9.993728356380645E-4,0.0010409373153748619,0.0010840148554642924,0.0011287987379994466,0.0011752060959946736,0.0012221000784029938,0.0012697192861478948,0.001317264927129829,0.0013642078964479333,0.0014104812256177247,0.0014549590645874264,0.0014977470072593,0.0015388600589552551,0.0015785690420550952,0.0016145390982125062,0.0016463001907804295,0.001675457722173868,0.0017043926993450219,0.00173341138

In [12]:
df.densityPlot("depth")

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.5.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="dy10Hc"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 
 (function() {
 // ----------
 
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"depth",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density"
},
"stat":"identity",
"data":{
"density":[5.230453106561777E-5,5.3911617195861116E-5,5.5429408858707796E-5,5.684832419092773E-5,5.815934934544032E-5,5.9354149521594184E-5,6.0425175806032464E-5,6.136576648148915E-5,6.217024154116761E-5,6.283398924626051E-5,6.335354368094423E-5,6.372665238966932E-5,6.39523333223435E-5,6.403092046041357E-5,6.396409764718019E-5,6.375492029523355E-5,6.340782478914414E-5,6.29286255392248E-5,6.232449976941949E-5,6.160396023678779E-5,6.0776816179834433E-5,5.985412287692605E-5,5.8848120263784604E-5,5.777216111083256E-5,5.6640629297998836E-5,5.546884874820338E-5,5.4272983593500015E-5,5.3069930152738465E-5,5.1877201300018556E-5,5.0712803802928126E-5,4.959510921248584E-5,4.8542718896800274E-5,4.757432383141776E-5,4.6708559794512225E-5,4.5963858667210076E-5,4.535829661042406E-5,4.490943998059124E-5,4.463418995761896E-5,4.454862698784E-5,4.466785629031035E-5,4.5005855832497786E-5,4.557532834619024E-5,4.6387559120014564E-5,4.745228146400851E-5,4.877755188612248E-5,5.036963714171528E-5,5.2232915406176036E-5,5.4369793869025694E-5,5.678064504699298E-5,5.946376405627345E-5,6.241534896441358E-5,6.562950615558034E-5,6.909828238691663E-5,7.281172488800266E-5,7.67579704623304E-5,8.092336409386244E-5,8.529260705044237E-5,8.984893391878795E-5,9.457431741499969E-5,9.944969920394289E-5,1.0445524434605878E-4,1.0957061638782996E-4,1.147752695395567E-4,1.2004875385858596E-4,1.253710288944428E-4,1.3072278086994336E-4,1.3608573818321132E-4,1.4144297983106227E-4,1.467792312833601E-4,1.5208114238648635E-4,1.5733754204450234E-4,1.625396647180381E-4,1.6768134418912526E-4,1.7275917055752302E-4,1.777726070499674E-4,1.8272406392493034E-4,1.876189275263667E-4,1.9246554336329892E-4,1.9727515294948103E-4,2.0206178500964788E-4,2.0684210252691715E-4,2.1163520795091704E-4,2.1646240969047927E-4,2.213469537617305E-4,2.2631372513734943E-4,2.3138892393278812E-4,2.3659972205948698E-4,2.4197390636495069E-4,2.475395145584056E-4,2.53324470384226E-4,2.593562245509151E-4,2.6566140785058945E-4,2.722655027136964E-4,2.791925391388855E-4,2.86464820522635E-4,2.941026843930051E-4,3.021243024336988E-4,3.1054552347662133E-4,3.193797623530276E-4,3.2863793663616273E-4,3.3832845239446465E-4,3.4845723911805385E-4,3.5902783299781487E-4,3.7004150674309734E-4,3.8149744313929545E-4,3.933929485901561E-4,4.057237019822907E-4,4.1848403337230064E-4,4.3166722625162404E-4,4.45265836511744E-4,4.592720207324154E-4,4.7367786606642765E-4,4.884757138114718E-4,5.036584687552726E-4,5.192198865626187E-4,5.351548318460051E-4,5.514595001240097E-4,5.681315976164994E-4,5.851704737411224E-4,6.025772022432814E-4,6.203546080889071E-4,6.385072385477908E-4,6.570412782628412E-4,6.75964409501988E-4,6.95285620186767E-4,7.150149636461187E-4,7.35163275317031E-4,7.557418527678699E-4,7.767621064215682E-4,7.982351891732656E-4,8.201716137056374E-4,8.425808666851457E-4,8.654710291615528E-4,8.888484123857922E-4,9.127172179098172E-4,9.370792302463626E-4,9.619335495634301E-4,9.872763708913968E-4,0.0010131008151600214,0.0010393968160921213,0.0010661510655991982,0.0010933470188925207,0.0011209649590824596,0.0011489821196317383,0.0011773728616936991,0.0012061089021424061,0.0012351595870198156,0.0012644922042142107,0.001294072328465457,0.0013238641912813288,0.001353831068053578,0.0013839356745838048,0.0014141405653614872,0.0014444085262676459,0.00147470295

In case you want to provide input and weights using column selection DSL,
it's a bit different from the usual one — you should assign `x`
input and (optionally) `weight` throw invocation eponymous functions:

In [13]:
df.densityPlot(adjust = 0.5) {
    x(depth)
    weight(coeff)
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.5.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="q2L9sE"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 
 (function() {
 // ----------
 
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"depth",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"densityWeighted"
},
"stat":"identity",
"data":{
"x":[158.58602236898395,159.8429286538177,161.0998349386514,162.35674122348516,163.61364750831888,164.87055379315262,166.12746007798637,167.3843663628201,168.64127264765384,169.89817893248758,171.1550852173213,172.41199150215505,173.66889778698877,174.9258040718225,176.18271035665626,177.43961664148998,178.69652292632372,179.95342921115747,181.2103354959912,182.46724178082493,183.72414806565865,184.9810543504924,186.23796063532615,187.49486692015986,188.7517732049936,190.00867948982733,191.26558577466108,192.52249205949482,193.77939834432854,195.0363046291623,196.293210913996,197.55011719882975,198.8070234836635,200.06392976849722,201.32083605333096,202.57774233816468,203.83464862299843,205.09155490783218,206.34846119266592,207.60536747749964,208.8622737623334,210.1191800471671,211.37608633200085,212.6329926168346,213.88989890166832,215.14680518650206,216.40371147133578,217.66061775616953,218.91752404100328,220.174430325837,221.43133661067074,222.68824289550446,223.9451491803382,225.20205546517195,226.4589617500057,227.71586803483942,228.97277431967314,230.22968060450688,231.48658688934063,232.74349317417438,234.0003994590081,235.2573057438418,236.51421202867556,237.7711183135093,239.02802459834305,240.28493088317677,241.5418371680105,242.79874345284423,244.05564973767798,245.31255602251173,246.56946230734545,247.8263685921792,249.0832748770129,250.34018116184666,251.5970874466804,252.85399373151415,254.11090001634787,255.3678063011816,256.62471258601533,257.8816188708491,259.1385251556828,260.3954314405165,261.65233772535026,262.909244010184,264.16615029501776,265.4230565798515,266.6799628646852,267.93686914951894,269.1937754343527,270.45068171918643,271.7075880040202,272.96449428885387,274.2214005736877,275.47830685852136,276.7352131433551,277.99211942818886,279.24902571302255,280.50593199785635,281.76283828269004,283.0197445675238,284.27665085235753,285.5335571371913,286.790463422025,288.0473697068587,289.30427599169246,290.5611822765262,291.8180885613599,293.0749948461937,294.3319011310274,295.58880741586114,296.8457137006949,298.10261998552863,299.3595262703624,300.61643255519607,301.8733388400298,303.13024512486356,304.3871514096973,305.64405769453106,306.90096397936475,308.1578702641985,309.41477654903224,310.671682833866,311.92858911869973,313.1854954035334,314.4424016883672,315.6993079732009,316.95621425803466,318.2131205428684,319.4700268277021,320.7269331125359,321.9838393973696,323.24074568220334,324.4976519670371,325.7545582518708,327.0114645367046,328.26837082153827,329.525277106372,330.78218339120576,332.03908967603945,333.29599596087326,334.55290224570695,335.8098085305407,337.06671481537444,338.32362110020813,339.58052738504193,340.8374336698756,342.09433995470937,343.3512462395431,344.6081525243768,345.8650588092106,347.1219650940443,348.37887137887805,349.6357776637118,350.8926839485455,352.1495902333793,353.406496518213,354.6634028030467,355.92030908788047,357.1772153727142,358.43412165754796,359.69102794238165,360.9479342272154,362.20484051204915,363.4617467968829,364.71865308171664,365.9755593665503,367.2324656513841,368.4893719362178,369.74627822105157,371.0031845058853,372.260090790719,373.5169970755528,374.7739033603865,376.03080964522024,377.287715930054,378.5446222148877,379.8015284997215,381.0584347845552,382.31534

`densityPlot` plot can be configured with `.configure {}` extension — it opens context that combines area,
`StatDensity` and plot context.
That means you can configure bars settings, mappings using `StatDensity` dataset and any plot adjustments:

In [14]:
df.densityPlot {
    x(depth)
}.configure {
    // Area + StatDensity + PlotContext
    // Can't add new layer
    // Can add area mapping, including for `Stat.*` columns
    fillColor(Stat.scaled) // doesn't work properly for now
    alpha = 0.6
    // Can configure general plot adjustments
    layout {
        title = "Configured `densityPlot` plot"
        size = 600 to 350
    }
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.5.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="KwEZsf"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 
 (function() {
 // ----------
 
 var plotSpec={
"ggtitle":{
"text":"Configured `densityPlot` plot"
},
"mapping":{
},
"data":{
"density":[5.230453106561777E-5,5.3911617195861116E-5,5.5429408858707796E-5,5.684832419092773E-5,5.815934934544032E-5,5.9354149521594184E-5,6.0425175806032464E-5,6.136576648148915E-5,6.217024154116761E-5,6.283398924626051E-5,6.335354368094423E-5,6.372665238966932E-5,6.39523333223435E-5,6.403092046041357E-5,6.396409764718019E-5,6.375492029523355E-5,6.340782478914414E-5,6.29286255392248E-5,6.232449976941949E-5,6.160396023678779E-5,6.0776816179834433E-5,5.985412287692605E-5,5.8848120263784604E-5,5.777216111083256E-5,5.6640629297998836E-5,5.546884874820338E-5,5.4272983593500015E-5,5.3069930152738465E-5,5.1877201300018556E-5,5.0712803802928126E-5,4.959510921248584E-5,4.8542718896800274E-5,4.757432383141776E-5,4.6708559794512225E-5,4.5963858667210076E-5,4.535829661042406E-5,4.490943998059124E-5,4.463418995761896E-5,4.454862698784E-5,4.466785629031035E-5,4.5005855832497786E-5,4.557532834619024E-5,4.6387559120014564E-5,4.745228146400851E-5,4.877755188612248E-5,5.036963714171528E-5,5.2232915406176036E-5,5.4369793869025694E-5,5.678064504699298E-5,5.946376405627345E-5,6.241534896441358E-5,6.562950615558034E-5,6.909828238691663E-5,7.281172488800266E-5,7.67579704623304E-5,8.092336409386244E-5,8.529260705044237E-5,8.984893391878795E-5,9.457431741499969E-5,9.944969920394289E-5,1.0445524434605878E-4,1.0957061638782996E-4,1.147752695395567E-4,1.2004875385858596E-4,1.253710288944428E-4,1.3072278086994336E-4,1.3608573818321132E-4,1.4144297983106227E-4,1.467792312833601E-4,1.5208114238648635E-4,1.5733754204450234E-4,1.625396647180381E-4,1.6768134418912526E-4,1.7275917055752302E-4,1.777726070499674E-4,1.8272406392493034E-4,1.876189275263667E-4,1.9246554336329892E-4,1.9727515294948103E-4,2.0206178500964788E-4,2.0684210252691715E-4,2.1163520795091704E-4,2.1646240969047927E-4,2.213469537617305E-4,2.2631372513734943E-4,2.3138892393278812E-4,2.3659972205948698E-4,2.4197390636495069E-4,2.475395145584056E-4,2.53324470384226E-4,2.593562245509151E-4,2.6566140785058945E-4,2.722655027136964E-4,2.791925391388855E-4,2.86464820522635E-4,2.941026843930051E-4,3.021243024336988E-4,3.1054552347662133E-4,3.193797623530276E-4,3.2863793663616273E-4,3.3832845239446465E-4,3.4845723911805385E-4,3.5902783299781487E-4,3.7004150674309734E-4,3.8149744313929545E-4,3.933929485901561E-4,4.057237019822907E-4,4.1848403337230064E-4,4.3166722625162404E-4,4.45265836511744E-4,4.592720207324154E-4,4.7367786606642765E-4,4.884757138114718E-4,5.036584687552726E-4,5.192198865626187E-4,5.351548318460051E-4,5.514595001240097E-4,5.681315976164994E-4,5.851704737411224E-4,6.025772022432814E-4,6.203546080889071E-4,6.385072385477908E-4,6.570412782628412E-4,6.75964409501988E-4,6.95285620186767E-4,7.150149636461187E-4,7.35163275317031E-4,7.557418527678699E-4,7.767621064215682E-4,7.982351891732656E-4,8.201716137056374E-4,8.425808666851457E-4,8.654710291615528E-4,8.888484123857922E-4,9.127172179098172E-4,9.370792302463626E-4,9.619335495634301E-4,9.872763708913968E-4,0.0010131008151600214,0.0010393968160921213,0.0010661510655991982,0.0010933470188925207,0.0011209649590824596,0.0011489821196317383,0.0011773728616936991,0.0012061089021424061,0.0012351595870198156,0.0012644922042142107,0.001294072328465457,0.0013238641912813288,0.001353831068053578,0.0013839356745838048,0.0014141405653614872,0.0014444085262676459,0.001474702954889054,0.0015049882222960042,0.0015352300109333797,0.001565395624169256,0.0015954542640034763,0.0016253772744270576,0.001655138348907564,0.001684713701423338,0.0017140822013505443,0.0017432254732

## Grouped `statDensity`

`statDensity` can be applied for grouped data —
statistics will be calculated on each group independently but with equal categories.
This application returns a new `GroupBy`
dataset with the same keys as the old one but with `StatDensity` groups instead of old ones.

In [15]:
// Create two samples from normal distribution with different mean/std
val rangesA = NormalDistribution(500.0, 100.0).sample(5000).toList()
val rangesB = NormalDistribution(400.0, 80.0).sample(5000).toList()

// Gather them into `DataFrame` with "A" and "B" keys in the "category" column
val rangesDF = dataFrameOf(
    "range" to rangesA + rangesB,
    "category" to List(5000) { "A" } + List(5000) { "B" }
)
rangesDF.head()

<iframe onload="o_resize_iframe_out_5()" style="width:100%;" class="result_container" id="iframe_out_5" frameBorder="0" srcdoc=" <html>
 <head>
 <style type="text/css">
 :root {
 --background: #fff;
 --background-odd: #f5f5f5;
 --background-hover: #d9edfd;
 --header-text-color: #474747;
 --text-color: #848484;
 --text-color-dark: #000;
 --text-color-medium: #737373;
 --text-color-pale: #b3b3b3;
 --inner-border-color: #aaa;
 --bold-border-color: #000;
 --link-color: #296eaa;
 --link-color-pale: #296eaa;
 --link-hover: #1a466c;
}

:root[theme="dark"], :root [data-jp-theme-light="false"], .dataframe_dark{
 --background: #303030;
 --background-odd: #3c3c3c;
 --background-hover: #464646;
 --header-text-color: #dddddd;
 --text-color: #b3b3b3;
 --text-color-dark: #dddddd;
 --text-color-medium: #b2b2b2;
 --text-color-pale: #737373;
 --inner-border-color: #707070;
 --bold-border-color: #777777;
 --link-color: #008dc0;
 --link-color-pale: #97e1fb;
 --link-hover: #00688e;
}

p.dataframe_description {
 color: var(--text-color-dark);
}

table.dataframe {
 font-family: "Helvetica Neue", Helvetica, Arial, sans-serif;
 font-size: 12px;
 background-color: var(--background);
 color: var(--text-color-dark);
 border: none;
 border-collapse: collapse;
}

table.dataframe th, td {
 padding: 6px;
 border: 1px solid transparent;
 text-align: left;
}

table.dataframe th {
 background-color: var(--background);
 color: var(--header-text-color);
}

table.dataframe td {
 vertical-align: top;
 white-space: nowrap;
}

table.dataframe th.bottomBorder {
 border-bottom-color: var(--bold-border-color);
}

table.dataframe tbody > tr:nth-child(odd) {
 background: var(--background-odd);
}

table.dataframe tbody > tr:nth-child(even) {
 background: var(--background);
}

table.dataframe tbody > tr:hover {
 background: var(--background-hover);
}

table.dataframe a {
 cursor: pointer;
 color: var(--link-color);
 text-decoration: none;
}

table.dataframe tr:hover > td a {
 color: var(--link-color-pale);
}

table.dataframe a:hover {
 color: var(--link-hover);
 text-decoration: underline;
}

table.dataframe img {
 max-width: fit-content;
}

table.dataframe th.complex {
 background-color: var(--background);
 border: 1px solid var(--background);
}

table.dataframe .leftBorder {
 border-left-color: var(--inner-border-color);
}

table.dataframe .rightBorder {
 border-right-color: var(--inner-border-color);
}

table.dataframe .rightAlign {
 text-align: right;
}

table.dataframe .expanderSvg {
 width: 8px;
 height: 8px;
 margin-right: 3px;
}

table.dataframe .expander {
 display: flex;
 align-items: center;
}

/* formatting */

table.dataframe .null {
 color: var(--text-color-pale);
}

table.dataframe .structural {
 color: var(--text-color-medium);
 font-weight: bold;
}

table.dataframe .dataFrameCaption {
 font-weight: bold;
}

table.dataframe .numbers {
 color: var(--text-color-dark);
}

table.dataframe td:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}

table.dataframe tr:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}


:root {
 --scroll-bg: #f5f5f5;
 --scroll-fg: #b3b3b3;
}
:root[theme="dark"], :root [data-jp-theme-light="false"]{
 --scroll-bg: #3c3c3c;
 --scroll-fg: #97e1fb;
}
body {
 scrollbar-color: var(--scroll-fg) var(--scroll-bg);
}
body::-webkit-scrollbar {
 width: 10px; /* Mostly for vertical scrollbars */
 height: 10px; /* Mostly for horizontal scrollbars */
}
body::-webkit-scrollbar-thumb {
 background-color: var(--scroll-fg);
}
body::-webkit-scrollbar-track {
 background-color: var(--scroll-bg);
}
 </style>
 </head>
 <body>
 <table class="dataframe" id="df_-1476395000"></table>

<p class="dataframe_description">DataFrame: rowsCount = 5, columnsCount = 2</p>

 </body>
 <script>
 (function () {
 window.DataFrame = window.DataFrame || new (function () {
 this.addTable = function (df) {
 let cols = df.cols;
 for (let i = 0; i < cols.length; i++) {
 for (let c of cols[i].children) {
 cols[c].parent = i;
 }
 }
 df.nrow = 

It has the following signature:

| range | category |
|-------|----------|

In [16]:
// Group it by "category"
val groupedRangesDF = rangesDF.groupBy { category }
groupedRangesDF

<iframe onload="o_resize_iframe_out_6()" style="width:100%;" class="result_container" id="iframe_out_6" frameBorder="0" srcdoc=" <html>
 <head>
 <style type="text/css">
 :root {
 --background: #fff;
 --background-odd: #f5f5f5;
 --background-hover: #d9edfd;
 --header-text-color: #474747;
 --text-color: #848484;
 --text-color-dark: #000;
 --text-color-medium: #737373;
 --text-color-pale: #b3b3b3;
 --inner-border-color: #aaa;
 --bold-border-color: #000;
 --link-color: #296eaa;
 --link-color-pale: #296eaa;
 --link-hover: #1a466c;
}

:root[theme="dark"], :root [data-jp-theme-light="false"], .dataframe_dark{
 --background: #303030;
 --background-odd: #3c3c3c;
 --background-hover: #464646;
 --header-text-color: #dddddd;
 --text-color: #b3b3b3;
 --text-color-dark: #dddddd;
 --text-color-medium: #b2b2b2;
 --text-color-pale: #737373;
 --inner-border-color: #707070;
 --bold-border-color: #777777;
 --link-color: #008dc0;
 --link-color-pale: #97e1fb;
 --link-hover: #00688e;
}

p.dataframe_description {
 color: var(--text-color-dark);
}

table.dataframe {
 font-family: "Helvetica Neue", Helvetica, Arial, sans-serif;
 font-size: 12px;
 background-color: var(--background);
 color: var(--text-color-dark);
 border: none;
 border-collapse: collapse;
}

table.dataframe th, td {
 padding: 6px;
 border: 1px solid transparent;
 text-align: left;
}

table.dataframe th {
 background-color: var(--background);
 color: var(--header-text-color);
}

table.dataframe td {
 vertical-align: top;
 white-space: nowrap;
}

table.dataframe th.bottomBorder {
 border-bottom-color: var(--bold-border-color);
}

table.dataframe tbody > tr:nth-child(odd) {
 background: var(--background-odd);
}

table.dataframe tbody > tr:nth-child(even) {
 background: var(--background);
}

table.dataframe tbody > tr:hover {
 background: var(--background-hover);
}

table.dataframe a {
 cursor: pointer;
 color: var(--link-color);
 text-decoration: none;
}

table.dataframe tr:hover > td a {
 color: var(--link-color-pale);
}

table.dataframe a:hover {
 color: var(--link-hover);
 text-decoration: underline;
}

table.dataframe img {
 max-width: fit-content;
}

table.dataframe th.complex {
 background-color: var(--background);
 border: 1px solid var(--background);
}

table.dataframe .leftBorder {
 border-left-color: var(--inner-border-color);
}

table.dataframe .rightBorder {
 border-right-color: var(--inner-border-color);
}

table.dataframe .rightAlign {
 text-align: right;
}

table.dataframe .expanderSvg {
 width: 8px;
 height: 8px;
 margin-right: 3px;
}

table.dataframe .expander {
 display: flex;
 align-items: center;
}

/* formatting */

table.dataframe .null {
 color: var(--text-color-pale);
}

table.dataframe .structural {
 color: var(--text-color-medium);
 font-weight: bold;
}

table.dataframe .dataFrameCaption {
 font-weight: bold;
}

table.dataframe .numbers {
 color: var(--text-color-dark);
}

table.dataframe td:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}

table.dataframe tr:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}


:root {
 --scroll-bg: #f5f5f5;
 --scroll-fg: #b3b3b3;
}
:root[theme="dark"], :root [data-jp-theme-light="false"]{
 --scroll-bg: #3c3c3c;
 --scroll-fg: #97e1fb;
}
body {
 scrollbar-color: var(--scroll-fg) var(--scroll-bg);
}
body::-webkit-scrollbar {
 width: 10px; /* Mostly for vertical scrollbars */
 height: 10px; /* Mostly for horizontal scrollbars */
}
body::-webkit-scrollbar-thumb {
 background-color: var(--scroll-fg);
}
body::-webkit-scrollbar-track {
 background-color: var(--scroll-bg);
}
 </style>
 </head>
 <body>
 <table class="dataframe" id="df_-1476394998"></table>

<p class="dataframe_description">GroupBy</p>

 </body>
 <script>
 (function () {
 window.DataFrame = window.DataFrame || new (function () {
 this.addTable = function (df) {
 let cols = df.cols;
 for (let i = 0; i < cols.length; i++) {
 for (let c of cols[i].children) {
 cols[c].parent = i;
 }
 }
 df.nrow = 0
 for (let i = 0; i < df.cols.leng

Now we have a `GroupBy` with a signature

<table>
  <thead>
    <tr>
      <th>key: [category]</th>
      <th>group: DataFrame[range|category]</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td>A</td>
      <td>A-Group</td>
    </tr>
    <tr>
      <td>B</td>
      <td>B-Group</td>
    </tr>
  </tbody>
</table>

In [17]:
groupedRangesDF.statDensity { x(range) }

<iframe onload="o_resize_iframe_out_8()" style="width:100%;" class="result_container" id="iframe_out_8" frameBorder="0" srcdoc=" <html>
 <head>
 <style type="text/css">
 :root {
 --background: #fff;
 --background-odd: #f5f5f5;
 --background-hover: #d9edfd;
 --header-text-color: #474747;
 --text-color: #848484;
 --text-color-dark: #000;
 --text-color-medium: #737373;
 --text-color-pale: #b3b3b3;
 --inner-border-color: #aaa;
 --bold-border-color: #000;
 --link-color: #296eaa;
 --link-color-pale: #296eaa;
 --link-hover: #1a466c;
}

:root[theme="dark"], :root [data-jp-theme-light="false"], .dataframe_dark{
 --background: #303030;
 --background-odd: #3c3c3c;
 --background-hover: #464646;
 --header-text-color: #dddddd;
 --text-color: #b3b3b3;
 --text-color-dark: #dddddd;
 --text-color-medium: #b2b2b2;
 --text-color-pale: #737373;
 --inner-border-color: #707070;
 --bold-border-color: #777777;
 --link-color: #008dc0;
 --link-color-pale: #97e1fb;
 --link-hover: #00688e;
}

p.dataframe_description {
 color: var(--text-color-dark);
}

table.dataframe {
 font-family: "Helvetica Neue", Helvetica, Arial, sans-serif;
 font-size: 12px;
 background-color: var(--background);
 color: var(--text-color-dark);
 border: none;
 border-collapse: collapse;
}

table.dataframe th, td {
 padding: 6px;
 border: 1px solid transparent;
 text-align: left;
}

table.dataframe th {
 background-color: var(--background);
 color: var(--header-text-color);
}

table.dataframe td {
 vertical-align: top;
 white-space: nowrap;
}

table.dataframe th.bottomBorder {
 border-bottom-color: var(--bold-border-color);
}

table.dataframe tbody > tr:nth-child(odd) {
 background: var(--background-odd);
}

table.dataframe tbody > tr:nth-child(even) {
 background: var(--background);
}

table.dataframe tbody > tr:hover {
 background: var(--background-hover);
}

table.dataframe a {
 cursor: pointer;
 color: var(--link-color);
 text-decoration: none;
}

table.dataframe tr:hover > td a {
 color: var(--link-color-pale);
}

table.dataframe a:hover {
 color: var(--link-hover);
 text-decoration: underline;
}

table.dataframe img {
 max-width: fit-content;
}

table.dataframe th.complex {
 background-color: var(--background);
 border: 1px solid var(--background);
}

table.dataframe .leftBorder {
 border-left-color: var(--inner-border-color);
}

table.dataframe .rightBorder {
 border-right-color: var(--inner-border-color);
}

table.dataframe .rightAlign {
 text-align: right;
}

table.dataframe .expanderSvg {
 width: 8px;
 height: 8px;
 margin-right: 3px;
}

table.dataframe .expander {
 display: flex;
 align-items: center;
}

/* formatting */

table.dataframe .null {
 color: var(--text-color-pale);
}

table.dataframe .structural {
 color: var(--text-color-medium);
 font-weight: bold;
}

table.dataframe .dataFrameCaption {
 font-weight: bold;
}

table.dataframe .numbers {
 color: var(--text-color-dark);
}

table.dataframe td:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}

table.dataframe tr:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}


:root {
 --scroll-bg: #f5f5f5;
 --scroll-fg: #b3b3b3;
}
:root[theme="dark"], :root [data-jp-theme-light="false"]{
 --scroll-bg: #3c3c3c;
 --scroll-fg: #97e1fb;
}
body {
 scrollbar-color: var(--scroll-fg) var(--scroll-bg);
}
body::-webkit-scrollbar {
 width: 10px; /* Mostly for vertical scrollbars */
 height: 10px; /* Mostly for horizontal scrollbars */
}
body::-webkit-scrollbar-thumb {
 background-color: var(--scroll-fg);
}
body::-webkit-scrollbar-track {
 background-color: var(--scroll-bg);
}
 </style>
 </head>
 <body>
 <table class="dataframe" id="df_-1476394990"></table>

<p class="dataframe_description">GroupBy</p>

 </body>
 <script>
 (function () {
 window.DataFrame = window.DataFrame || new (function () {
 this.addTable = function (df) {
 let cols = df.cols;
 for (let i = 0; i < cols.length; i++) {
 for (let c of cols[i].children) {
 cols[c].parent = i;
 }
 }
 df.nrow = 0
 for (let i = 0; i < df.cols.leng

After `statDensity` applying it's still a `GroupBy` but with different signature of `group` -
all groups have the same signature as usual `DataFrame` after `statDensity` applying (i.e. `StatDensityFrame`):

<table>
  <thead>
    <tr>
      <th>key: [drv]</th>
      <th>group: StaDensityFrame</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td>"A"</td>
      <td>"A"-Group</td>
    </tr>
    <tr>
      <td>"B"</td>
      <td>"B"-Group</td>
    </tr>
  </tbody>
</table>

As you can see, we did indeed do a `statDensity` transformation within groups, the grouping keys did not change.
The plotting process doesn't change much — we do everything the same.

In [18]:
groupedRangesDF.plot {
    statDensity(range) {
        line {
            x(Stat.x)
            y(Stat.density)
        }
    }
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.5.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="SUzesI"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 
 (function() {
 // ----------
 
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"group":"&merged_groups"
},
"stat":"identity",
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B",

As you can see, there are two lines because we have two groups of data.
To distinguish them, we need to add mapping to the color from the key.
This is convenient — the key is available in the context

In [19]:
groupedRangesDF.plot {
    statDensity(range) {
        line {
            x(Stat.x)
            y(Stat.density)
            color(key.category)
        }
    }
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.5.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="124BWn"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 
 (function() {
 // ----------
 
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"color",
"discrete":true
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"color":"category",
"group":"&merged_groups"
},
"stat":"identity",
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B"

The `densityPlot()` layer also works.
Moreover, if we have exactly one grouping key, a mapping from it to `fillColor`
and `borderLine.color` will be created by default.

In [20]:
groupedRangesDF.plot {
    densityPlot(range)
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.5.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="uojCUD"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 
 (function() {
 // ----------
 
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"range",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"fill",
"discrete":true
},{
"aesthetic":"color",
"discrete":true
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"fill":"category",
"color":"category",
"group":"&merged_groups"
},
"stat":"identity",
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B

We can customize it like we used to. From the differences — access to `key` columns:

In [21]:
groupedRangesDF.plot {
    densityPlot(range) {
        // Customize scale of default mapping
        fillColor(key.category) {
            scale = categorical("A" to Color.GREEN, "B" to Color.ORANGE)
        }
        borderLine.color = Color.BLACK
        alpha = 0.5
    }
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.5.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="obUWNi"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 
 (function() {
 // ----------
 
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"range",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"fill",
"values":["#3ba272","#fc8452"],
"limits":["A","B"]
},{
"aesthetic":"color",
"discrete":true
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"fill":"category",
"color":"category",
"group":"&merged_groups"
},
"stat":"identity",
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B"

Also, we can stack areas (for that we need `x` coordinates to match — use `trim = true`):

In [22]:
groupedRangesDF.plot {
    // Use trim
    densityPlot(range, trim = true) {
        // Adjust position of areas from different groups
        position = Position.stack()
        alpha = 0.8
    }
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.5.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="vX0VIG"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 
 (function() {
 // ----------
 
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"range",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"fill",
"discrete":true
},{
"aesthetic":"color",
"discrete":true
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"fill":"category",
"color":"category",
"group":"&merged_groups"
},
"stat":"identity",
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B

`densityPlot` plot for `GroupBy` (i.e. `GroupBy.densityPlot(statDensityArgs)` extensions) works as well:

In [23]:
groupedRangesDF.densityPlot("range", bandWidth = BandWidth.value(10.0))

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.5.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="2j04ud"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 
 (function() {
 // ----------
 
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"range",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"fill",
"discrete":true
},{
"aesthetic":"color",
"discrete":true
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"fill":"category",
"color":"category",
"group":"&merged_groups"
},
"stat":"identity",
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B

... and can be configured the same way:

In [24]:
groupedRangesDF.densityPlot(n = 750, trim = true, adjust = 0.75) { x(range) }.configure {
    alpha = 0.6
    position = Position.stack()
    // Can access key column by name as `String`
    fillColor("category") { scale = categoricalColorBrewer(BrewerPalette.Qualitative.Dark2) }
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.5.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="ZW7nHV"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 
 (function() {
 // ----------
 
 var plotSpec={
"mapping":{
},
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B

### Inside `groupBy{}` plot context

We can apply `groupBy` modification to the initial dataset and build a density plot with grouped data the same way:

In [25]:
rangesDF.plot {
    groupBy(category) {
        densityPlot(range)
    }
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.5.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="8VgEpt"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 
 (function() {
 // ----------
 
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"range",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"fill",
"discrete":true
},{
"aesthetic":"color",
"discrete":true
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"fill":"category",
"color":"category",
"group":"&merged_groups"
},
"stat":"identity",
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B